In [37]:
from lyricsgenius import Genius
import pandas as pd
import numpy as np
from secret import *


In [38]:
genius = Genius(genius_token, remove_section_headers=True)

df = pd.read_csv('reduced_main_dataset.csv')


In [39]:
def grab_lyrics(artist_name : str, track_name : str):
    song = genius.search_song(artist=artist_name, title=track_name)
    return song.lyrics
    

In [40]:
for i in df.index:
    try:
        artist_name = df['artists'].iloc[i]
        track_name = df['track_name'].iloc[i]
        df['lyrics'].iloc[i] = grab_lyrics(artist_name=artist_name, track_name=track_name)
    except Exception:
        df['lyrics'].iloc[i] == ""
        continue


Searching for "Comedy" by Gen Hoshino...
Done.
Searching for "Ghost - Acoustic" by Ben Woodward...


/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pandas/core/indexing.py:1732: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


No results found for: 'Ghost - Acoustic Ben Woodward'
Searching for "To Begin Again" by Ingrid Michaelson;ZAYN...
Done.
Searching for "Can't Help Falling In Love" by Kina Grannis...
Done.
Searching for "Hold On" by Chord Overstreet...
Done.
Searching for "Days I Will Remember" by Tyrone Wells...
Done.
Searching for "Say Something" by A Great Big World;Christina Aguilera...
Done.
Searching for "I'm Yours" by Jason Mraz...
Done.
Searching for "Lucky" by Jason Mraz;Colbie Caillat...
Done.
Searching for "Hunger" by Ross Copperman...
Done.
Searching for "Give Me Your Forever" by Zack Tabudlo...
Done.
Searching for "I Won't Give Up" by Jason Mraz...
Done.
Searching for "Solo" by Dan Berk...
Done.
Searching for "Bad Liar" by Anna Hamilton...
Done.
Searching for "Hold On - Remix" by Chord Overstreet;Deepend...
Done.
Searching for "Falling in Love at a Coffee Shop" by Landon Pigg...
Done.
Searching for "ily (i love you baby)" by Andrew Foy;Renee Foy...
No results found for: 'ily (i love you bab

In [41]:
df.to_csv('reduced_main_dataset_with_lyrics.csv')

In [ ]:
# df['lyrics'].value_counts()[""]
print(len(df[df['lyrics'] == NaN]))
display(df.iloc[85])

In [52]:
nan_values = df[df['lyrics'].isna()]

print (len(nan_values))

14855


Here I'm dropping all songs (rows) that have null values for the lyrics column. They don't have lyrics so I can't use Tf-Idf on them.

In [58]:
df_without_null_lyrics = df.dropna()

In [59]:
df_without_null_lyrics.shape

(37486, 23)

In [60]:
nan_values = df_without_null_lyrics[df_without_null_lyrics['lyrics'].isna()]
print(len(nan_values))

0


Some of the api requests returned a list of singles for the artist rather than the lyrics for the song. I know if the cell is incorrecet because the beginning of the string will read "<Month><YYYY><"Singles Release Calendar">. This is BNF for the type of string I need to watch out for. Example: "August 2020 Singles Release Calendar Lyrics8/1" If the lyrics cell begins like this, I need to remove this row.  There are 465 instances of this. Which will leave me with 37,486 - 465 = 37,021 songs.

df_clean holds all songs with viable lyrics. Meaning no null values and no random lists that were returned from the api.

In [131]:
df_clean = df_without_null_lyrics[df_without_null_lyrics['lyrics'].str.contains("Singles Release Calendar") == False]

In [132]:
df_clean.shape

(37021, 23)

In [ ]:
df_clean.to_csv('clean_main_dataset.csv')

In [135]:
df_clean['word_count'] = df_clean['lyrics'].str.count(' ') + 1

/var/folders/b8/tkxd7yxj1672bq9d4m_3xmhh0000gn/T/ipykernel_47942/1893300271.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clean['word_count'] = df_clean['lyrics'].str.count(' ') + 1


If the number of words in the song cell are greater than 5000 I'm assuming that those are not lyrics to the song. There are some songs in other language so I don't actually know. But some of the songs have word count of over 30,000 and those are way too high to be any song lyrics.

In [143]:
df_clean = df_clean[df_clean['word_count'] <= 1000]

In [144]:
df_clean.shape

(33029, 24)

In [145]:
df_clean = df_clean[df_clean['lyrics'].str.contains("New Music Friday") == False]
df_clean = df_clean[df_clean['lyrics'].str.contains("Songs of the Same Title") == False]
df_clean = df_clean[df_clean['lyrics'].str.contains("Album Release Calendar") == False]
df_clean = df_clean[df_clean['lyrics'].str.contains("My Spotify Playist Lyrics") == False]
df_clean = df_clean[df_clean['lyrics'].str.contains("Spotify Singles: Complete Collection Lyrics") == False]

In [146]:
df_clean.shape

(33029, 24)

In [194]:
df_clean.to_csv('clean_reduced_dataset.csv')

In [148]:
df_clean = df_clean[df_clean['lyrics'].str.contains("My Spotify Playist") == False]

In [149]:
df_clean.shape

(33029, 24)

In [193]:
df_clean = df_clean[df_clean['lyrics'].str.contains("List of unreleased songs") == False]
df_clean.shape

(32231, 24)